# Climate-Friendly Food Systems (CFFS) Labelling Project

### The University of British Columbia

#### Created by Silvia Huang, CFFS Data Analyst
****

## Part II: Data Cleaning

## Set up and Import Libraries

In [1]:
#pip install -r requirements.txt

In [2]:
import numpy as np
import pandas as pd
import pdpipe as pdp
import matplotlib.pyplot as plt
import glob
import os
import csv
from itertools import islice
from decimal import Decimal
import xml.etree.ElementTree as et
from xml.etree.ElementTree import parse
import openpyxl
import pytest
from datetime import datetime

C:\Users\smvan\anaconda3\lib\site-packages\pdpipe\col_generation.py:12: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm


In [3]:
# Set the root path, change the the current working directory into the project folder
path = "C:/Users/smvan/CFFS-S23/CFFS-22-23"
# path = os.getcwd()
print(path)
os.chdir(path)

C:/Users/smvan/CFFS-S23/CFFS-22-23


In [4]:
# Enable reading data table in the scrolling window if you prefer
pd.set_option("display.max_rows", None, "display.max_columns", None)

***

## Import Preprocessed Datasets

In [5]:
# Read Items_List.csv
# Reading csv file: C:/Users/smvan/CFFS-S23/CFFS-22-23/data/preprocessed/Items_List.csv
Items = pd.read_csv(os.path.join(os.getcwd(), "data", "preprocessed", "Items_List.csv"))
Items.dtypes

ItemId             object
Description        object
CaseQty           float64
CaseUOM            object
PakQty            float64
PakUOM             object
InventoryGroup     object
dtype: object

In [6]:
# Display first 5 rows
Items.head()

ItemId                     Description  CaseQty CaseUOM  PakQty PakUOM  \
0   I-7631                  5 SPICE POWDER      1.0      ea     1.0     lb   
1   I-2353   9"X6" 2-COMPARTMENT CLAMSHELL    200.0      CT     1.0     CT   
2  I-43239                AGAR AGAR POWDER    500.0       g     1.0      g   
3  I-57481     AHA WATER SP BLUEB POM PET      24.0    each     1.0   each   
4  I-57484  AHA WATER SP PEACH HONEY PET       24.0    each     1.0   each   

  InventoryGroup  
0         SPICES  
1    DISPOSABLES  
2         SPICES  
3       BEVERAGE  
4       BEVERAGE

In [7]:
# There are 486 rows and 7 columns
Items.shape

(1341, 7)

In [8]:
# Read Ingredients_List.csv
Ingredients = pd.read_csv(os.path.join(os.getcwd(), "data", "preprocessed", "Ingredients_List.csv"))
Ingredients.dtypes

IngredientId     object
Qty             float64
Uom              object
Conversion      float64
InvFactor       float64
Recipe           object
dtype: object

In [9]:
# Display first 5 rows
Ingredients.head()

IngredientId    Qty Uom  Conversion  InvFactor   Recipe
0      P-48933   1.00  Kg    1.000000     1.0000  P-10113
1      P-18746   1.00  Kg    1.000000     1.0000  P-10241
2       I-3388   1.00   L    1.000000     0.3058  P-10496
3       I-4658   2.27  Kg    2.204620     0.6942  P-10496
4       I-1813  30.00  ml    0.033814     9.3750  P-10502

In [10]:
# There are 3278 rows and 6 columns
Ingredients.shape

(16050, 6)

In [11]:
# Read Preps_List.csv
Preps = pd.read_csv(os.path.join(os.getcwd(), "data", "preprocessed", "Preps_List.csv"))
Preps.dtypes

PrepId             object
Description        object
PakQty            float64
PakUOM             object
InventoryGroup     object
dtype: object

In [12]:
# Display first 5 rows
Preps.head()

PrepId                   Description  PakQty PakUOM       InventoryGroup
0  P-61322                   AIOLI|Pesto     4.0      L  ZDONT USE OK - PREP
1  P-61009         ALF|Flatbread|Brisket     1.0     un                  NaN
2  P-26184                   BAKED|Beans     9.0     Kg                 PREP
3  P-53798             BAKED|Berry Crisp    45.0     Kg                  NaN
4  P-64511  Baked|Brocoli|Mushroom|Pasta     6.0     Kg                  NaN

In [13]:
# There are 546 rows and 5 columns
Preps.shape

(1742, 5)

In [14]:
# Read Product_List.csv that was created from 1_data preprocessing
Products = pd.read_csv(os.path.join(os.getcwd(), "data", "preprocessed", "Products_List.csv"))
Products.dtypes

ProdId         object
Description    object
SalesGroup     object
dtype: object

In [15]:
# Display first 5 rows
Products.head()

ProdId                     Description           SalesGroup
0  R-67294  $1 OWN MUG ETHICAL BEAN COFFEE             BEVERAGE
1  R-62976                         ADD CUP       OK - GRAB & GO
2  R-31006                        ADD|Beef  OK - CUSTOM KITCHEN
3  R-31131                     ADD|Chicken  OK - CUSTOM KITCHEN
4  R-30154                    ADD|Crackers  OK - CUSTOM KITCHEN

In [16]:
# There are 223 rows and 3 columns
Products.shape

(2005, 3)

In [17]:
# Read Coversions_List.csv that was created from 1_data preprocessing
Conversions = pd.read_csv(os.path.join(os.getcwd(), "data", "preprocessed", "Conversions_List.csv"))
Conversions.dtypes

ConversionId       object
Multiplier        float64
ConvertFromQty    float64
ConvertFromUom     object
ConvertToQty      float64
ConvertToUom       object
dtype: object

In [18]:
# Display first 5 rows
Conversions.head()

ConversionId  Multiplier  ConvertFromQty ConvertFromUom  ConvertToQty  \
0          NaN    1.000000             1.0            XXX          1.00   
1          NaN    0.877193             1.0          1.14L          1.14   
2          NaN    0.666667             1.0           1.5L          1.50   
3          NaN    0.571429             1.0         1.75 L          1.75   
4          NaN    0.500000             1.0             2L          2.00   

  ConvertToUom  
0            L  
1            L  
2            L  
3            L  
4            L

In [19]:
# There are 270 rows and 6 columns
Conversions.shape

(444, 6)

***
## Update Conversion List

In [20]:
# Add the specific conversion info from the newly-processed data to a unit conversion database
Update_Conv = pd.read_csv(os.path.join(os.getcwd(), "data", "cleaning", "update", "Conv_UpdateConv.csv"))
Update_Conv

ConversionId  Multiplier  ConvertFromQty ConvertFromUom  ConvertToQty  \
0        I-67659    0.008818           1.000           each       113.398   
1        I-28697    0.005181           1.000             ea       193.000   
2        I-47441    0.005181           1.000             ea       193.000   
3         I-1905    0.012500           1.000             CT        80.000   
4        I-47440    0.005051           1.000             ea       198.000   
5        I-13327    0.003077           0.750            pak       243.750   
6        I-54484    0.004545           1.000           each       220.000   
7         I-2501    0.009091           0.250            pak        27.500   
8        I-52609    0.004219           1.000             ea       237.000   
9        I-52636    0.004219           1.000             ea       237.000   
10        I-2772    0.003571           1.000             CT       280.000   
11       I-20347    0.004000           0.800            PTN       200.000   
12       I-54756    0.007055           1.000           each       141.748   
13       I-41251    0.005051           1.000             ea       198.000   
14        I-2833    0.004000           0.100             CT        25.000   
15       I-54761    0.017544           1.000           each        57.000   
16       I-54755    0.017544           1.000           each        57.000   
17       I-54759    0.017544           1.000           each        57.000   
18       I-63749    0.002415           1.000          414ML       414.000   
19       I-54758    0.017544           1.000           each        57.000   
20       I-53847    0.002415           1.000          414ML       414.000   
21       I-34313    0.000092           0.010             cs       109.000   
22       I-19639    0.010000           1.000             ea       100.000   
23       I-63683    0.022099           1.000             ea        45.250   
24       I-19700    0.009091           1.000            pak       110.000   
25        I-3902    0.006024           1.000             CT       166.000   
26       I-63690    0.013158           1.000             ea        76.000   
27       I-48660    0.005882           0.780             ea       132.600   
28        I-2546    0.002358           0.250             CT       106.000   
29        I-1727    0.001408           1.000          710ml       710.000   
30        I-2118    0.004000           0.750            PTN       187.500   
31        I-2778    0.008850           1.000             CT       113.000   
32       I-63698    0.035242           3.000             ea        85.125   
33        I-2116    0.004000           0.250            PTN        62.500   
34        I-2120    0.004000           1.000            PTN       250.000   
35       I-32271    0.035714           1.000          slice        28.000   
36       I-38717    0.008850           1.000             CT       113.000   
37       I-31549    0.011111           1.000          slice        90.000   
38       I-53226    0.005357           0.220             ea        41.070   
39       I-32265    0.035398           0.500             ea        14.125   
40       I-41807    0.025000           1.000             ea        40.000   
41       I-41805    0.025000           1.000           each        40.000   
42       I-63977    0.002203           1.000             ea       454.000   
43       I-43988    0.028571           1.000             ea        35.000   
44       I-42899    0.007692           1.000             ea       130.000   
45       I-13970    0.004000           0.500             ea       125.000   
46       I-54757    0.017544           1.000           each        57.000   
47       I-51331    0.002939           1.000             ea       340.194   
48       I-38957    0.008547           1.000             ea       117.000   
49       I-41804    0.090909           1.000             ea        11.000   
50       I-41800    0.090909           1.000             ea        11.000   


In [21]:
# return dataframe with null values
# There are no null values
subset_conv = Update_Conv[Update_Conv["Multiplier"].isna()]
subset_conv

Empty DataFrame
Columns: [ConversionId, Multiplier, ConvertFromQty, ConvertFromUom, ConvertToQty, ConvertToUom]
Index: []

In [22]:
# takes a data frame and assigns a new column called Multiplier to the dataframe
# uses iterrows() to iterate through the rows.Then subset_conv will have a new column named Multiplier with the computed values.
def assign_multiplier(df):
    for ind, row in df.iterrows():
        df.loc[ind, "Multiplier"] = row["ConvertFromQty"] / row["ConvertToQty"]
        
assign_multiplier(subset_conv)

# May 8th change: We want to 
assign_multiplier(Update_Conv)
#subset_conv

In [23]:
# convert dataframe to csv file
Update_Conv = pd.concat([Update_Conv, subset_conv], axis=0)
Update_Conv.to_csv("data/cleaning/update/Conv_UpdateConv.csv", index=False)

In [24]:
# retrieves the value in the 'ConversionId' column using Update_Conv.loc[index, 'ConversionId'] 
# and assigns it to the variable Id. 

# row: a Series (1-d array in pandas) You can access the individual values of the row using the column headers as keys to the
# like row['column_name'].

# if the IDs of Update_Conv are the same IDs as Conversions then we drop it from the Conversions dataframe


# CHANGED ON AUG 7
# for index, row in Update_Conv.iterrows():
#     Id = Update_Conv.loc[index, 'ConversionId']
#     Conversions.drop(Conversions[Conversions['ConversionId'] == Id].index, inplace = True)
    

for index, row in Update_Conv.iterrows():
    Id = row['ConversionId'] 
    if Id in Conversions['ConversionId'].values:
        Conversions.drop(Conversions[Conversions['ConversionId'] == Id].index, inplace=True)
    else:
        print(f"Warning: 'ConversionId' {Id} not found in Conversions DataFrame. Skipping drop operation.")


In [25]:
# combine two data frames, reset the index and remove any duplicates in the concatenated data frame, 
# and return the resulting data frame.

# Added comments below on May 8th

# frames variable is created as a list of two DataFrames, Conversions and Update_Conv.
# pd.concat() function is used to concatenate the two DataFrames vertically (i.e., stack one on top of the other). 

# drop_duplicates() method is used to remove any duplicate rows from the concatenated DataFrame based on all columns. 
# The resulting DataFrame has only unique rows.

# The resulting DataFrame is assigned back to the variable Conversions,

# drop = True ensures that the old index is not added as a new column to the dataframe 
# inplace=False parameter ensures that a new DataFrame is returned rather than modifying 
# the original Conversions DataFrame in place.

frames = [Conversions, Update_Conv]
Conversions = pd.concat(frames).reset_index(drop=True, inplace=False).drop_duplicates()

In [26]:
Conversions

ConversionId   Multiplier  ConvertFromQty ConvertFromUom  ConvertToQty  \
0            NaN     1.000000          1.0000            XXX        1.0000   
1            NaN     0.877193          1.0000          1.14L        1.1400   
2            NaN     0.666667          1.0000           1.5L        1.5000   
3            NaN     0.571429          1.0000         1.75 L        1.7500   
4            NaN     0.500000          1.0000             2L        2.0000   
5            NaN     0.250000          1.0000             4L        4.0000   
6            NaN     0.083333          1.0000           FOOT       12.0000   
7            NaN     0.062500          1.0000            16L       16.0000   
8            NaN     0.059172          1.0000         1/2LTR       16.9000   
9            NaN     0.039370          1.0000          750ML       25.4000   
10           NaN     0.033333          1.0000        KEG 30L       30.0000   
11           NaN     0.025974          1.0000         1140ml       38.5000   
12           NaN     0.025000          1.0000        full in       40.0000   
13           NaN     0.020000          1.0000        KEG 50L       50.0000   
14           NaN     0.017065          1.0000        KEG 59L       58.6000   
15           NaN     0.016667          1.0000           HOUR       60.0000   
16           NaN     0.002000          1.0000          500ML      500.0000   
17           NaN     0.001538          1.0000          650ML      650.0000   
18           NaN     0.001515          1.0000          660ML      660.0000   
19           NaN     0.001429          1.0000          700ML      700.0000   
20           NaN     0.001408          1.0000          710ml      710.0000   
21           NaN     0.001333          1.0000          750ML      750.0000   
22           NaN     0.000592          1.0000         keg50L     1690.0000   
23           NaN     0.000504          1.0000         keg59L     1984.0000   
24           NaN     2.000000          2.0000            cup        1.0000   
25           NaN     2.000000          2.0000             pt        1.0000   
26           NaN     2.000000          2.0000           Tbsp        1.0000   
27           NaN     3.000000          3.0000            tsp        1.0000   
28           NaN     4.000000          4.0000             qt        1.0000   
29           NaN     8.000000          8.0000          fl oz        1.0000   
30           NaN    16.000000         16.0000             oz        1.0000   
31           NaN    28.349500         28.3495              g        1.0000   
32           NaN    29.573500         29.5735             ml        1.0000   
33           NaN    35.211268        100.0000          fl oz        2.8400   
34           NaN  1000.000000       1000.0000              g        1.0000   
35           NaN  1000.000000       1000.0000             mg        1.0000   
36           NaN  1000.000000       1000.0000             ml        1.0000   
37      Iqq-1093     0.011765          1.0000             CT       85.0000   
38        I-1100     1.000000          1.0000             CT        1.0000   
39        I-1120     0.020000          1.0000             CT       50.0000   
40        I-1195     0.023810          1.0000             CT       42.0000   
41        I-1197     0.013333          1.0000             CT       75.0000   
42        I-1232     0.033333          1.0000           LOAF       30.0000   
43        I-1277     0.008850          1.0000             CT      113.0000   
44        I-1791     0.032258          1.0000          fl oz       31.0000   
45        I-1791     0.004032          1.0000            cup      248.0000   
46        I-1813     0.032787          1.0000          fl oz       30.5000   
47        I-1813     0.004098          1.0000            cup      244.0000   
48        I-1814     0.032787          1.0000          fl oz       30.5000   
49        I-1814     0.004098          1.0000            cup      244.0000   
50        I-1815     0.032

In [27]:
# Convert the DataFrame: Conversions into a csv file called Conversions_Added.csv
path = os.path.join(os.getcwd(), "data", "cleaning", "Conversions_Added.csv")
Conversions.to_csv(path, index = False, header = True)

### Create Unit Converter

In [28]:
# Import standard unit conversion information and construct a dataframe
Std_Unit = pd.read_csv(os.path.join(os.getcwd(), "data", "external", "standard_conversions.csv"))
Std_Unit.head()

Multiplier  ConvertFromQty ConvertFromUom  ConvertToQty ConvertToUom
0     4.92890               1            tsp       4.92890           ml
1    14.78700               1           Tbsp      14.78700           ml
2   946.35000               1             qt     946.35000           ml
3   473.17625               1             pt     473.17625           ml
4    28.34950               1             oz      28.34950            g

In [29]:
# Seperate uoms that converted to 'ml' or 'g'
# Below we create 2 lists. 
# list_unit contains list of unit of measurements that are being converted to milliliters 
# solid_unit contains a list of unit of measurements that are being converted to grams
# tolist() converts a Pandas Series or an array to a python list. 

liquid_unit = Std_Unit.loc[Std_Unit['ConvertToUom'] == 'ml', 'ConvertFromUom'].tolist()
solid_unit = Std_Unit.loc[Std_Unit['ConvertToUom'] == 'g', 'ConvertFromUom'].tolist()

In [30]:
# Construct a standard unit converter
def std_converter(qty, uom):
    if uom in Std_Unit['ConvertFromUom'].tolist():
        multiplier = Std_Unit.loc[Std_Unit['ConvertFromUom'] == uom, 'Multiplier']
        Qty = float(qty)*float(multiplier)
        Uom = Std_Unit.loc[Std_Unit['ConvertFromUom'] == uom, 'ConvertToUom'].values[0]
    else:
        Qty = qty
        Uom = uom
    return (Qty, Uom)

In [31]:
# Convert pounds to grams
std_converter(0.25,'lb')

(113.398, 'g')

In [32]:
# Test the std_converter
assert std_converter(0.25,'lb') == (113.398, 'g')

In [33]:
# Construct a unit converter for specific ingredients

# After this line below, spc_cov contains only the non-empty values from the 'ConversionId' column of the Conversions DataFrame.
spc_cov = list(filter(None, Conversions['ConversionId'].tolist()))


# Comments for spc_converter:
# The function checks if ingredient is in the liquid_unit or solid_unit lists. If so, it calls std_converter(qty, uom) to 
# convert the quantity and UOM to a standardized unit.

# If uom is not in liquid_unit or solid_unit it checks if ingre is in spc_cov, if it is and the ConvertToUom is equal to grams 
# then the function applies the factor to the qty argument to convert it to the standardized unit, and returns the result as
# a tuple containing the converted quantity and uom. If no conversion found, then it calls std_converter(qty, uom)

# If uom not in liquid_unit or solid_unit and if ingre is not in spc_cov then the function calls std_converter(qty, uom)

def spc_converter(ingre, qty, uom):
    if uom in liquid_unit + solid_unit:
        return std_converter(qty, uom)
    elif ingre in spc_cov:
        conversion = Conversions.loc[(Conversions['ConversionId'] == ingre) & (Conversions['ConvertFromUom'] == uom)
                                    & (Conversions['ConvertToUom'] == 'g')]
        multiplier = conversion['Multiplier']
        if multiplier.empty:
            return std_converter(qty, uom)
        else: 
            Qty = float(qty)/float(multiplier)
            Uom = conversion['ConvertToUom'].values[0]
            return (Qty, Uom)
    else:
        return std_converter(qty, uom)

In [34]:
spc_cov

[nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 'Iqq-1093',
 'I-1100',
 'I-1120',
 'I-1195',
 'I-1197',
 'I-1232',
 'I-1277',
 'I-1791',
 'I-1791',
 'I-1813',
 'I-1813',
 'I-1814',
 'I-1814',
 'I-1815',
 'I-1815',
 'I-1820',
 'I-1820',
 'I-1821',
 'I-1821',
 'I-1827',
 'I-1827',
 'I-2074',
 'I-2074',
 'I-2159',
 'I-2159',
 'I-2159',
 'I-2205',
 'I-2205',
 'I-2205',
 'I-2207',
 'I-2207',
 'I-2207',
 'I-2217',
 'I-2218',
 'I-2218',
 'I-2218',
 'I-2220',
 'I-2220',
 'I-2220',
 'I-2221',
 'I-2221',
 'I-2221',
 'I-2236',
 'I-2236',
 'I-2236',
 'I-2244',
 'I-2248',
 'I-2248',
 'I-2251',
 'I-2251',
 'I-2251',
 'I-2252',
 'I-2252',
 'I-2252',
 'I-2252',
 'I-2254',
 'I-2254',
 'I-2306',
 'I-2310',
 'I-2933',
 'I-3074',
 'I-3113',
 'I-3113',
 'I-3113',
 'I-3141',
 'I-3143',
 'I-3143',
 'I-3144',
 'I-3144',
 'I-3144',
 'I-31

In [35]:
# spc_cov2 is the same as spc_cov but without null values labelled as "nan" in the list
import math
spc_cov2 = [item for item in spc_cov if not(pd.isnull(item)) == True]
spc_cov2

['Iqq-1093',
 'I-1100',
 'I-1120',
 'I-1195',
 'I-1197',
 'I-1232',
 'I-1277',
 'I-1791',
 'I-1791',
 'I-1813',
 'I-1813',
 'I-1814',
 'I-1814',
 'I-1815',
 'I-1815',
 'I-1820',
 'I-1820',
 'I-1821',
 'I-1821',
 'I-1827',
 'I-1827',
 'I-2074',
 'I-2074',
 'I-2159',
 'I-2159',
 'I-2159',
 'I-2205',
 'I-2205',
 'I-2205',
 'I-2207',
 'I-2207',
 'I-2207',
 'I-2217',
 'I-2218',
 'I-2218',
 'I-2218',
 'I-2220',
 'I-2220',
 'I-2220',
 'I-2221',
 'I-2221',
 'I-2221',
 'I-2236',
 'I-2236',
 'I-2236',
 'I-2244',
 'I-2248',
 'I-2248',
 'I-2251',
 'I-2251',
 'I-2251',
 'I-2252',
 'I-2252',
 'I-2252',
 'I-2252',
 'I-2254',
 'I-2254',
 'I-2306',
 'I-2310',
 'I-2933',
 'I-3074',
 'I-3113',
 'I-3113',
 'I-3113',
 'I-3141',
 'I-3143',
 'I-3143',
 'I-3144',
 'I-3144',
 'I-3144',
 'I-3145',
 'I-3145',
 'I-3146',
 'I-3146',
 'I-3149',
 'I-3159',
 'I-3223',
 'I-3223',
 'I-3224',
 'I-3224',
 'I-3225',
 'I-3225',
 'I-3229',
 'I-3237',
 'I-3284',
 'I-3284',
 'I-3284',
 'I-3321',
 'I-3321',
 'I-3348',
 'I-3356

In [36]:
# Here we pass in the ingredient (I-1120) the quantity of the ingredient (1) and the unit of measurement: CT -> count
# This gives us the number of grams of that ingredient
spc_converter('I-1120', 1, 'CT')

(50.0, 'g')

In [37]:
# Identify the ones that are not in the conversion list 

In [38]:
Conversions.loc[Conversions["ConversionId"] == "I-14190"]

Empty DataFrame
Columns: [ConversionId, Multiplier, ConvertFromQty, ConvertFromUom, ConvertToQty, ConvertToUom]
Index: []

In [39]:
c_list = Conversions["ConversionId"].unique()
"I-68700" in c_list

False

In [40]:
spc_converter("I-14190", 1, "LOAF")

(1, 'LOAF')

In [41]:
spc_converter('I-47530', 7, 'ea')

(210.0, 'g')

In [42]:
# Test the spc_converter
# spc_converter('I-1120', 1, 'CT')
#assert spc_converter('I-1120', 1, 'CT') == (134.99995275001655, 'g')

***
## Items with Non-standard Units

In [43]:
Ingredients

IngredientId       Qty     Uom    Conversion  InvFactor   Recipe
0          P-48933     1.000      Kg  1.000000e+00     1.0000  P-10113
1          P-18746     1.000      Kg  1.000000e+00     1.0000  P-10241
2           I-3388     1.000       L  1.000000e+00     0.3058  P-10496
3           I-4658     2.270      Kg  2.204620e+00     0.6942  P-10496
4           I-1813    30.000      ml  3.381406e-02     9.3750  P-10502
5           I-6026    15.000       g  1.000000e+00     4.6875  P-10502
6          I-60772     3.000       L  1.000000e+00     0.9375  P-10502
7          P-26020   100.000       g  1.000000e-03    31.2500  P-10502
8          P-41466   200.000       g  1.000000e+00    62.5000  P-10502
9          P-45879     7.500      Kg  1.000000e+00     1.8750  P-10873
10         I-11312     3.000       g  3.527399e-02     0.2727  P-11375
11          I-3223     5.640       L  1.000000e+00     0.5127  P-11375
12          I-3245   200.000       g  1.000000e+00    18.1818  P-11375
13          I-3501    20.000       g  1.000000e-03     1.8182  P-11375
14          I-3642    10.000       g  1.000000e+00     0.9091  P-11375
15          I-4341     2.000      CT  1.000000e+00     0.1818  P-11375
16          I-4742  2270.000       g  2.204620e-03   206.3636  P-11375
17         I-47774   125.000      ml  1.000000e-03    11.3636  P-11375
18          I-4918    30.000       g  2.204620e-03     2.7273  P-11375
19          I-5983     4.000       L  1.000000e+00     0.3636  P-11375
20          I-6028   250.000       g  1.000000e-03    22.7273  P-11375
21          I-6443   500.000      ml  3.381406e-02    45.4545  P-11375
22          I-6820   450.000       g  1.000000e-03    40.9091  P-11375
23         P-18226   120.000      ml  1.000000e-03    10.9091  P-11375
24         P-26020   125.000       g  1.000000e-03    11.3636  P-11375
25         P-34880   125.000       g  1.000000e-03    11.3636  P-11375
26         I-12176     4.000       g  1.000000e-03     0.3636  P-12112
27          I-1813   400.000      ml  3.381406e-02    36.3636  P-12112
28          I-3337     4.000       L  1.000000e+00     0.3636  P-12112
29          I-3387   100.000      ml  1.000000e-03     9.0909  P-12112
30          I-3447   199.000      ml  1.000000e+00    18.0909  P-12112
31          I-3507     6.000       L  1.000000e+00     0.5455  P-12112
32          I-3639    30.000       g  1.000000e+00     2.7273  P-12112
33          I-3642     4.000       g  1.000000e+00     0.3636  P-12112
34         I-47774   200.000      ml  1.000000e-03    18.1818  P-12112
35          I-3435     1.000      Kg  1.012840e+00     0.0500  P-12502
36          I-3992    20.000      Kg  1.000000e+00     1.0000  P-12502
37          I-4589     1.000      Kg  2.204620e+00     0.0500  P-12502
38          I-4598     1.000      Kg  1.250000e+00     0.0500  P-12502
39          I-4745     2.000      Kg  2.204620e+00     0.1000  P-12502
40          I-5983    25.000       L  1.000000e+00     1.2500  P-12502
41          I-4598     1.000      CT  1.000000e+00     0.0013  P-12954
42          I-3284    15.000      ml  2.000000e-03     0.6000  P-13326
43          I-3291   510.000       g  1.000000e-03    20.4000  P-13326
44          I-3660    10.000       g  1.000000e-03     0.4000  P-13326
45          I-3661   170.000       g  1.000000e-03     6.8000  P-13326
46          I-6026     2.500       g  1.000000e+00     0.1000  P-13326
47          I-8060   510.000       g  1.000000e+00    20.4000  P-13326
48         I-11842     2.000    LOAF  1.000000e+00     0.8818  P-13648
49          I-3388    60.000      ml  1.000000e-03    26.4550  P-13648
50          I-3642     5.000       g  1.000000e+00     2.2046  P-13648
51          I-6006    60.000      ml  1.000000e-03    26.4550  P-13648
52          I-6026     5.000       g  1.000000e+00     2.2046  P-13648
53          I-3451     2.560       L  1.000000e+00     1.2800  P-13933
54          I-2157     1.000      Kg  1.000000e+00     1.0000  P-14069
55          I-3619     5.000  

In [44]:
Items

ItemId                     Description   CaseQty CaseUOM     PakQty  \
0       I-7631                  5 SPICE POWDER      1.00      ea      1.000   
1       I-2353   9"X6" 2-COMPARTMENT CLAMSHELL    200.00      CT      1.000   
2      I-43239                AGAR AGAR POWDER    500.00       g      1.000   
3      I-57481     AHA WATER SP BLUEB POM PET      24.00    each      1.000   
4      I-57484  AHA WATER SP PEACH HONEY PET       24.00    each      1.000   
5      I-56025  AHA WATER SP WATERMLN LIME PET     24.00    each      1.000   
6       I-3617         ALLSPICE GROUND SHAKER       8.00    each    454.000   
7       I-1851          ALMOND BEV - CHOCOLATE     24.00      CT      1.000   
8       I-1852           ALMOND BEV - ORIGINAL     24.00      CT      1.000   
9      I-61295       ALMOND BREEZE CHOC 240 ML      4.00      CT      1.000   
10     I-61294  ALMOND BREEZE VAN UNSWT 240 ML      4.00      CT      1.000   
11     I-44059                  ALMOND BUTTER*     10.00      Kg      1.000   
12     I-40957          ALMOND SLICED*BLANCHED      1.00     5KG   5000.000   
13     I-43652                    ANCHO CHILLI      1.20      Kg      1.000   
14      I-2852                   ANCHO POWDER       1.00     pak    227.000   
15      I-2853                ANCHOVIES FILLET      1.70      Kg      1.000   
16     I-11181                ANISE STAR WHOLE      8.00    each    240.000   
17     I-49238      ANNIE'S Choc Bunny Grahams     12.00      ea      1.000   
18     I-49236   ANNIE'S White Cheddar Bunnies     12.00      ea      1.000   
19     I-29389            APPLES DICED IQF FRZ      1.00     bag     18.180   
20      I-4456                  APPLES FUJI US     64.00      CT      1.000   
21      I-6775              APPLES GALA ROYAL     100.00      CT      1.000   
22      I-4461            APPLES GALA ROYAL BC    100.00      CT      1.000   
23      I-4458       APPLES GOLDEN DELICIOUSUS    113.00      CT      1.000   
24      I-4970  APPLES GRANN SMITH SLCD GRDE A      2.00     bag      2.500   
25      I-4271            APPLES GRANNY SMITH     113.00      ea      1.000   
26     I-13225      APPLES RED DELICIOUS 113CT      1.00      cs    113.000   
27     I-12177        APPLES SLCD GRANNY SMITH     10.00      Kg      1.000   
28      I-7957         APRICOTS DRIED TFC BULK     12.00     pak      0.450   
29      I-3117                 APRICOTS DRIED*      2.00     bag   1500.000   
30      I-4971     ARTICHOKE 1/4 SALAD CUT TFC      6.00  LG CAN      2.500   
31      I-4467              ASPARAGUS (STD) US     11.00      lb      1.000   
32      I-4473               AVOCADO (20CT) MX     20.00      CT      1.000   
33      I-4472                      AVOCADO MX     20.00      CT      1.000   
34      I-4973             AVOCADO PULP*CHUNKY     12.00     bag    454.000   
35     I-65741      BACON 2.5MM NATURALLY SMKD      5.00      Kg      1.000   
36     I-27410        BACON 3MM NATURALLY SMKD      5.00      Kg      1.000   
37      I-2305                  BACON PANCETTA      1.00      Kg      1.000   
38      I-1236       BAGEL MULTIGRAIN (6 PACK)     72.00    each      1.000   
39      I-1252         BAGEL PLAIN  SLICED 4OZ     72.00      CT      1.000   
40      I-1277       BAGEL SESAME SEED 6 PACK)     72.00    each      1.000   
41      I-1286      BAGEL WHOLE WHEAT (6 PACK)      6.00      CT      1.000   
42     I-57827      BAGUETTE CHICKEN TUSCAN GF      1.00    each      1.000   
43      I-1207                BAGUETTE FRENCH      24.00    each      1.000   
44     I-18089                  BAGUETTE WHITE     28.00      ea      1.000   
45      I-4495             BAK CHOY (60 LBS)US     50.00      lb      1.000   
46      I-4496                BAK CHOY BABY BC     30.00      lb      1.000   
47      I-4497                BAK CHOY BABY US     30.00      lb      1.000   
48      I-4491                     BAK CHOY BC     50.00      lb      1.000   
49      I-3118               BAKING PWDR MAGIC      6.00  

In [45]:
# Filter out the items whose unit information is unknown 

# We find the column names
col_names = list(Ingredients.columns.values)

# Create a Items_Nonstd list
Items_Nonstd = []

# If the unit of measurement is not grams or ml and ingredient id starts with I and the ingredient is not in ConversionId column of Conversions 
# then we add it to Items_Nonstd list
for index, row in Ingredients.iterrows():
    Ingre = Ingredients.loc[index,'IngredientId']
    Uom = Ingredients.loc[index,'Uom']
    if Uom not in ['g', 'ml'] and Uom not in liquid_unit + solid_unit and Ingre.startswith('I') and Ingre not in Conversions["ConversionId"].tolist():
        Dict = {}
        Dict.update(dict(row))
        Items_Nonstd.append(Dict)

# Create a DataFrame from Items_Nonstd list
Items_Nonstd = pd.DataFrame(Items_Nonstd, columns = col_names)
# Remove duplicate ingredients of the same properties so that Items_Nonstd has only unique rows. 
Items_Nonstd.drop_duplicates(subset=['IngredientId'], inplace=True,)
Items_Nonstd

IngredientId     Qty     Uom  Conversion  InvFactor   Recipe
0        I-11842   2.000    LOAF         1.0     0.8818  P-13648
1         I-1020   0.042   SHEET         1.0     0.0420  P-22029
2         I-1048   1.000   slice         1.0     1.0000  P-22030
3         I-1016   0.042   SHEET         1.0     0.0420  P-22032
4        I-11824   0.042   SHEET         1.0     0.0420  P-22037
5        I-56580   0.033   SHEET         1.0     0.0330  P-22042
6         I-1065   0.033   SHEET         1.0     0.0330  P-22049
7         I-1028   0.500      CT         1.0     0.5000  P-26170
8        I-64492   1.000    LOAF         1.0     0.0625  P-26234
9        I-19735   1.000      CT         1.0     0.1000  P-26318
10       I-15358  50.000      ea         1.0    55.1268  P-26393
11        I-1035   0.200      CT         1.0     0.2000  P-28369
12        I-1152   0.400      CT         1.0     0.4000  P-28369
13        I-1254   0.500      CT         1.0     0.5000  P-28369
14       I-17686   0.100      ea         1.0     0.1000  P-28369
15       I-17615   0.250   slice         1.0     0.2500  P-28372
16       I-17617   0.250   slice         1.0     0.2500  P-28372
17       I-19633   1.000     pak         1.0     0.1818  P-31170
19       I-18089   1.000      ea         1.0     0.2500  P-32729
20       I-30178   4.000   SHEET         1.0     0.0267  P-35733
21       I-24227   1.000    LOAF         1.0     0.0011  P-38282
22        I-1141  90.000      CT         1.0    40.0000  P-42353
24        I-1187   1.000    LOAF         1.0     0.0714  P-45430
25        I-9341  12.000      CT         1.0     0.0300  P-45790
27        I-1047  12.000      CT         1.0     1.0000  P-46861
29        I-8238   1.000      ea         1.0     1.0000  P-47243
31       I-31492   1.000      ea         1.0     1.0000  P-48485
33       I-16216   1.000   slice         1.0     1.0000  P-50510
34       I-25290   0.150    LOAF         1.0     0.1500  P-50511
35        I-9641   1.000    LOAF         1.0     0.0625  P-50725
36       I-24229   1.000    LOAF         1.0     0.0556  P-50799
37       I-13004   1.000      CT         1.0     0.0556  P-50809
38       I-11519   1.000     bag         1.0     0.0333  P-50853
39       I-15032   1.000    LOAF         1.0     0.0278  P-51992
42        I-4766  10.000      CT         1.0     8.0000  P-53753
43        I-3344  12.000     PTN         1.0     0.2667  P-53798
46       I-14190   1.000    LOAF         1.0     0.0455  P-54581
48        I-2586   1.000      CT         1.0     1.0000  P-54960
49        I-3103   1.000      CT         1.0     1.0000  P-55079
50        I-2672   1.000      CT         1.0     1.0000  P-55173
51        I-3688  16.000      CT         1.0    32.0000  P-55548
52        I-4504   4.000      ea         1.0     0.1600  P-55583
56       I-36765   2.000      ea         1.0     0.8000  P-56195
59       I-11518   5.000     bag         1.0     2.1739  P-57001
60        I-1034   1.000      CT         1.0     0.1667  P-57968
62       I-11855   1.000      CT         1.0     0.1667  P-57968
63        I-1186   0.025    LOAF         1.0     0.0042  P-57968
66       I-55414   1.000    each         1.0     0.1667  P-57968
67       I-25119   1.000      ea         1.0     1.0000  P-58285
69       I-57682   0.100    each         1.0     0.1000  P-58286
70        I-2661   0.056     PIE         1.0     0.0560  P-58297
71        I-2662   0.056     PIE         1.0     0.0560  P-58297
72        I-2667   0.056     PIE         1.0     0.0560  P-58297
73        I-1275   1.000    LOAF         1.0     0.0556  P-58309
74        I-1273   1.000    LOAF         1.0     0.1351  P-58370
78        I-1126  30.000      CT         1.0     3.7500  P-59557
79       I-50577   1.000  Dollar         1.0     2.0000  P-59674
81       I-37651  10.000    each         1.0     0.7143  P-59830
86        I-1127   1.000      CT         1.0     1.0000  P-60503
88       I-13302   0.250      CT         1.0     0.2500  P-60855
89        I-2771   0.250      CT       

In [46]:
# Assigning a Description column to the Items_Nonstd    
    
# for index, row in Items_Nonstd.iterrows():
#     idx = row['IngredientId']
#     descrp = Items.loc[Items['ItemId'] == idx, 'Description'].values[0]
#     Items_Nonstd.loc[index, 'Description'] = descrp


# CHANGE AUG 3:
for index, row in Items_Nonstd.iterrows():
    idx = row['IngredientId']
    filtered_items = Items.loc[Items['ItemId'] == idx, 'Description']
    if not filtered_items.empty:
        descrp = filtered_items.values[0]
        Items_Nonstd.loc[index, 'Description'] = descrp
    else:
        # Handle the case when there is no matching item for the given 'IngredientId'
        # For example, you can assign a default value or leave it unchanged.
        # Items_Nonstd.loc[index, 'Description'] = 'Not Found'
        pass



In [47]:
Items_Nonstd.head()

IngredientId    Qty    Uom  Conversion  InvFactor   Recipe  \
0      I-11842  2.000   LOAF         1.0     0.8818  P-13648   
1       I-1020  0.042  SHEET         1.0     0.0420  P-22029   
2       I-1048  1.000  slice         1.0     1.0000  P-22030   
3       I-1016  0.042  SHEET         1.0     0.0420  P-22032   
4      I-11824  0.042  SHEET         1.0     0.0420  P-22037   

                      Description  
0          SOURDOUGH LOAFCOUNTRY   
1     BAR NANAIMO SCORED 12X16IN   
2      CAKE BLACK*FOREST 12X16IN   
3  BROWNIE ROCKY ROAD 12X16IN TFC  
4  CAKE SHEET*BRNIE DBL CHOC FUDG

In [48]:
# Convert the Items_Nonstd DataFrame to a csv file
path = os.path.join(os.getcwd(), "data", "cleaning", "Items_Nonstd.csv")
Items_Nonstd.to_csv(path, index = False, header = True)

***
## Clean Preps Units

In [49]:
Preps

PrepId                     Description    PakQty PakUOM  \
0     P-61322                     AIOLI|Pesto     4.000      L   
1     P-61009           ALF|Flatbread|Brisket     1.000     un   
2     P-26184                     BAKED|Beans     9.000     Kg   
3     P-53798               BAKED|Berry Crisp    45.000     Kg   
4     P-64511    Baked|Brocoli|Mushroom|Pasta     6.000     Kg   
5     P-64689         BAKED|Chicken Thigh|FNH    34.000     Kg   
6     P-58410                   BAKED|Gnocchi     1.570     Kg   
7     P-26965        BAKED|Jalapeno Cornbread    12.000  piece   
8     P-50502                  BAKED|Meatball   310.000   each   
9     P-54644                  BAKED|Moussaka    16.000    PTN   
10    P-26218          BAKED|Mushroom Alfredo     5.000     lb   
11    P-54667     BAKED|Pasta|Bolognese Penne    16.000    PTN   
12    P-54666     BAKED|Pasta|Chicken Alfredo     6.176     Kg   
13    P-54664       BAKED|Pasta|Chorizo Penne     7.360     Kg   
14    P-56502        BAKED|Pasta|Shrimp Pesto     5.760     Kg   
15    P-54785          BAKED|Puff Pastry Tart     6.000   each   
16    P-49184        BAKED|Tofu|Almond Butter     4.000    PTN   
17    P-41065   BAKED|Tortellini|Mush Alfredo     4.500     Kg   
18    P-32729             BAKED|Warm Baguette     4.000   each   
19    P-26318                BAKEDPuff Pastry    10.000     ea   
20    P-50730               BASE|Hot and Sour  1000.000      g   
21    P-50731            BASE|Soaked Shiitake     1.000      L   
22    P-41321          BATCH| Fish Batter 2.0     1.200      L   
23    P-43206     BATCH| SMOOTHIE| Mango|16oz     4.000    PTN   
24    P-56953                  BATCH|Bannock    681.000      g   
25    P-61115                BATCH|Bean|Salad     2.350     Kg   
26    P-56828           BATCH|Beef Slider Mix     5.000     Kg   
27    P-44561   BATCH|Black Garlic Pork Belly     1.000     Kg   
28    P-61699  BATCH|Black Pepper Chili Sauce   800.000      g   
29    P-26682  BATCH|Black/White Sesame Seeds   907.186      g   
30    P-33866       BATCH|Burrito Bar Chicken    16.000     Kg   
31    P-56699   BATCH|Cauliflower Wings|Baked     1.000     Kg   
32    P-56431       BATCH|Chicken Apple Salad     5.443     Kg   
33    P-60977        BATCH|Chorizo House Made     1.300     Kg   
34    P-26333         BATCH|Citrus Herb Aioli     3.000      L   
35    P-59240           BATCH|Citrus Salsa|DS     1.000     Kg   
36    P-56629         BATCH|Corn Succotash|23     2.700     Kg   
37    P-56826          BATCH|Crab Cake|SLIDER   845.000      g   
38    P-26393  BATCH|Crisp Tortilla Strips|OK     0.907     Kg   
39    P-53088      BATCH|Enchiladas Vegan|POP     6.000   each   
40    P-56703        BATCH|Grainy Mustard Dip     1.000      L   
41    P-56398                 BATCH|Guacamole     2.750     Kg   
42    P-61137          BATCH|Hearty Veg Chili    14.000     Kg   
43    P-26075    BATCH|Jalapeno Cilantro Slaw     8.000     lb   
44    P-58654            BATCH|Jambalaya Tofu    13.500     Kg   
45    P-56328              BATCH|Jambalaya|23    30.000     Kg   
46    P-56117       BATCH|Japchae Stirfry 2.0     4.200     Kg   
47    P-55239         BATCH|Lettuce Wrap Pork     6.500     Kg   
48    P-55301         BATCH|Lettuce Wrap Tofu     6.500     Kg   
49    P-59241       BATCH|Med Salmon Spice|DS   500.000      g   
50    P-56427           BATCH|Olive Tapanade    325.000      g   
51    P-26134         BATCH|Pibil Pulled Pork     2.722     Kg   
52    P-56982         BATCH|Pineapple Mustard  1400.000     ml   
53    P-61104            BATCH|PoblanoFilling  4200.000      g   
54    P-39627               BATCH|Pulled Pork     2.720     Kg   
55    P-58350     BATCH|Pumpkin Coconut Sauce     5.000      L   
56    P-56534        BATCH|Red Coconut Curry      3.360     Kg   
57    P-59238          BATCH|Red Quinoa Salad     5.000     Kg   
58    P-33867              BATCH|Rice|Burrito     3.000     Kg   
59    P-26234      BATCH|Roasted Garlic Bread  

In [50]:
pd.read_csv("data/cleaning/update/Preps_UpdateUom.csv")

PrepId                     Description  PakQty   PakUOM  \
0    P-54697                 LEMON|Wedge 1/8    8.00     each   
1    P-35132      MARINATED|Lemon & Herb Chx  185.00       ea   
2    P-51992       YIELD|Bread|Sourdough 5/8   36.00    slice   
3    P-26234      BATCH|Roasted Garlic Bread   16.00       ea   
4    P-26170               GRILLED|NaanBread    1.00       ea   
5    P-16305              YIELD|Smokie (1pc)    1.00       ea   
6    P-26047      BOILED|Hard Boiled Eggs FT   50.00       ea   
7    P-26631      BRK|Pancake|Chocolate Chip   24.00       ea   
8    P-26057        FRIED|Sunny/Overeasy Egg    1.00       ea   
9    P-26056                  GRILLED|Tomato    1.00       ea   
10   P-44587                   GRL|FRIED|Egg    1.00       ea   
11   P-26481                POACHED|Egg|Soft    1.00       ea   
12   P-52620         GARNISH|Lime Mini Wedge    8.00    piece   
13   P-51510            SLICED|Avocado|1/4ea    4.00      PTN   
14   P-50398                 STICKS|Cucumber   12.00       CT   
15   P-61796         MARINADE|Bali Pork Chop   10.00       CT   
16   P-35713               BLACKENED|Chicken  185.00       ea   
17   P-51508              COOKED|Bacon|Slice    2.00    slice   
18   P-56795               COOKED|Burger 4oz    1.00       ea   
19   P-50809        YIELD|Country Loaf|Slice   18.00    slice   
20   P-50439                   FRIED|Tostada    3.00    piece   
21   P-57631           SKEWER|Greek Chicken     1.00     each   
22   P-26318                BAKEDPuff Pastry   10.00       ea   
23   P-61769          STEW|Chicken Pot Pie      8.00      PIE   
24   P-55238      MARINADE|Peri Peri Chicken  120.00       ea   
25   P-43635     ROASTED|Thai Chicken Thighs   25.00       ea   
26   P-37297              COOKED|Poached Egg    1.00     each   
27   P-53056          GRILLED|Roma Tomato|V2   13.00      PTN   
28   P-52222    YIELD|Pickle Spear ea 20-30g    1.00       ea   
29   P-26965        BAKED|Jalapeno Cornbread   12.00    piece   
30   P-28369                      COST|Bread    1.00       ea   
31   P-28372                    COST|Cheeses    1.00    slice   
32   P-28373                 COST|Vegetables    1.00       un   
33   P-52942          FILLING|Taco|Prawn|FLX    1.00     each   
34   P-51230           WINGS|Sauce Mix|ratio    1.00     srvg   
35   P-45255            YIELD|Chicken Strips   70.00    piece   
36   P-52994                YIELD|Prawn|TACO   35.00     each   
37   P-44392               PREP|Eggs|poached    8.00     each   
38   P-44506          SLICED|Avocado|Quarter    4.00     each   
39   P-43737             VEG|Soft Boiled Egg   20.00     each   
40   P-51826       GARNISH|Fried Rice Friday    1.00      PTN   
41   P-61508            GRILLED|Mexican Corn    8.00       ea   
42   P-46509               YIELD|Lettuce bun    3.00      PTN   
43    P-5548                    PREP|Lasagna    3.00  full in   
44    P-5960                   PREP|Tiramisu    1.00  full in   
45   P-61646              PREP|Chicken Wings  100.00       ea   
46   P-60970           SAND|IItalian Grander    1.00     each   
47   P-54644                  BAKED|Moussaka   16.00      PTN   
48   P-54667     BAKED|Pasta|Bolognese Penne   16.00      PTN   
49   P-53088      BATCH|Enchiladas Vegan|POP    6.00     each   
50   P-41727      BATCH|Lentil & Squash Stew   15.00      PTN   
51   P-62403           BATCH|RELLENO|Poblano    1.00     each   
52   P-53361           Batter|Pancake|Banana   24.00       ea   
53   P-51518        COOKED|4 oz Burger Patty    1.00      PTN   
54   P-55099        COOKED|6 oz Burger Patty    1.00      PTN   
55   P-47324         COOKED|Meatball Blended  180.00     each   
56   P-48863          DES|Brown Rice Pudding   12.00       CT   
57   P-51018          DOUGH|BreakfastBiscuit    5.00     each   
58   P-55422      FILLING|ChocCheeseCake|G&G    2.50       1L   
59   P-44353              FLEX|Savoury Chaat    7.00      PTN   
60   P-47610        FLEXlCyprus Mannoush 

In [51]:
# Creates 2 new columns called StdQty and StdUom in the Preps DataFrame. These columns contain NaN values
# Preparing to fill in these columns with standardized quantities and units of measurement 
Preps['StdQty'] = np.nan
Preps['StdUom'] = np.nan

In [52]:
# Convert uom into 'g' or 'ml' for each prep using the unit converter

# Retrieve the PrepId, PakQty, and PakUOM from the current row
# Pass these values to spc_converter, then we update the StdQty and StdUom columns of the current row with the converted values.
for index in Preps.index:
    PrepId = Preps.loc[index,'PrepId']
    Qty = Preps.loc[index,'PakQty']
    Uom = Preps.loc[index,'PakUOM']
    Preps.loc[index,'StdQty'] = spc_converter(PrepId, Qty, Uom)[0]
    Preps.loc[index,'StdUom'] = spc_converter(PrepId, Qty, Uom)[1]

In [53]:
Preps

PrepId                     Description    PakQty PakUOM  \
0     P-61322                     AIOLI|Pesto     4.000      L   
1     P-61009           ALF|Flatbread|Brisket     1.000     un   
2     P-26184                     BAKED|Beans     9.000     Kg   
3     P-53798               BAKED|Berry Crisp    45.000     Kg   
4     P-64511    Baked|Brocoli|Mushroom|Pasta     6.000     Kg   
5     P-64689         BAKED|Chicken Thigh|FNH    34.000     Kg   
6     P-58410                   BAKED|Gnocchi     1.570     Kg   
7     P-26965        BAKED|Jalapeno Cornbread    12.000  piece   
8     P-50502                  BAKED|Meatball   310.000   each   
9     P-54644                  BAKED|Moussaka    16.000    PTN   
10    P-26218          BAKED|Mushroom Alfredo     5.000     lb   
11    P-54667     BAKED|Pasta|Bolognese Penne    16.000    PTN   
12    P-54666     BAKED|Pasta|Chicken Alfredo     6.176     Kg   
13    P-54664       BAKED|Pasta|Chorizo Penne     7.360     Kg   
14    P-56502        BAKED|Pasta|Shrimp Pesto     5.760     Kg   
15    P-54785          BAKED|Puff Pastry Tart     6.000   each   
16    P-49184        BAKED|Tofu|Almond Butter     4.000    PTN   
17    P-41065   BAKED|Tortellini|Mush Alfredo     4.500     Kg   
18    P-32729             BAKED|Warm Baguette     4.000   each   
19    P-26318                BAKEDPuff Pastry    10.000     ea   
20    P-50730               BASE|Hot and Sour  1000.000      g   
21    P-50731            BASE|Soaked Shiitake     1.000      L   
22    P-41321          BATCH| Fish Batter 2.0     1.200      L   
23    P-43206     BATCH| SMOOTHIE| Mango|16oz     4.000    PTN   
24    P-56953                  BATCH|Bannock    681.000      g   
25    P-61115                BATCH|Bean|Salad     2.350     Kg   
26    P-56828           BATCH|Beef Slider Mix     5.000     Kg   
27    P-44561   BATCH|Black Garlic Pork Belly     1.000     Kg   
28    P-61699  BATCH|Black Pepper Chili Sauce   800.000      g   
29    P-26682  BATCH|Black/White Sesame Seeds   907.186      g   
30    P-33866       BATCH|Burrito Bar Chicken    16.000     Kg   
31    P-56699   BATCH|Cauliflower Wings|Baked     1.000     Kg   
32    P-56431       BATCH|Chicken Apple Salad     5.443     Kg   
33    P-60977        BATCH|Chorizo House Made     1.300     Kg   
34    P-26333         BATCH|Citrus Herb Aioli     3.000      L   
35    P-59240           BATCH|Citrus Salsa|DS     1.000     Kg   
36    P-56629         BATCH|Corn Succotash|23     2.700     Kg   
37    P-56826          BATCH|Crab Cake|SLIDER   845.000      g   
38    P-26393  BATCH|Crisp Tortilla Strips|OK     0.907     Kg   
39    P-53088      BATCH|Enchiladas Vegan|POP     6.000   each   
40    P-56703        BATCH|Grainy Mustard Dip     1.000      L   
41    P-56398                 BATCH|Guacamole     2.750     Kg   
42    P-61137          BATCH|Hearty Veg Chili    14.000     Kg   
43    P-26075    BATCH|Jalapeno Cilantro Slaw     8.000     lb   
44    P-58654            BATCH|Jambalaya Tofu    13.500     Kg   
45    P-56328              BATCH|Jambalaya|23    30.000     Kg   
46    P-56117       BATCH|Japchae Stirfry 2.0     4.200     Kg   
47    P-55239         BATCH|Lettuce Wrap Pork     6.500     Kg   
48    P-55301         BATCH|Lettuce Wrap Tofu     6.500     Kg   
49    P-59241       BATCH|Med Salmon Spice|DS   500.000      g   
50    P-56427           BATCH|Olive Tapanade    325.000      g   
51    P-26134         BATCH|Pibil Pulled Pork     2.722     Kg   
52    P-56982         BATCH|Pineapple Mustard  1400.000     ml   
53    P-61104            BATCH|PoblanoFilling  4200.000      g   
54    P-39627               BATCH|Pulled Pork     2.720     Kg   
55    P-58350     BATCH|Pumpkin Coconut Sauce     5.000      L   
56    P-56534        BATCH|Red Coconut Curry      3.360     Kg   
57    P-59238          BATCH|Red Quinoa Salad     5.000     Kg   
58    P-33867              BATCH|Rice|Burrito     3.000     Kg   
59    P-26234      BATCH|Roasted Garlic Bread  

In [54]:
# Save cleaned preps list to file
path = os.path.join(os.getcwd(), "data", "cleaning", "Preps_Unit_Cleaned.csv")
Preps.to_csv(path, index = False, header = True)

In [55]:
pd.read_csv("data/cleaning/update/Preps_UpdateUom.csv")

PrepId                     Description  PakQty   PakUOM  \
0    P-54697                 LEMON|Wedge 1/8    8.00     each   
1    P-35132      MARINATED|Lemon & Herb Chx  185.00       ea   
2    P-51992       YIELD|Bread|Sourdough 5/8   36.00    slice   
3    P-26234      BATCH|Roasted Garlic Bread   16.00       ea   
4    P-26170               GRILLED|NaanBread    1.00       ea   
5    P-16305              YIELD|Smokie (1pc)    1.00       ea   
6    P-26047      BOILED|Hard Boiled Eggs FT   50.00       ea   
7    P-26631      BRK|Pancake|Chocolate Chip   24.00       ea   
8    P-26057        FRIED|Sunny/Overeasy Egg    1.00       ea   
9    P-26056                  GRILLED|Tomato    1.00       ea   
10   P-44587                   GRL|FRIED|Egg    1.00       ea   
11   P-26481                POACHED|Egg|Soft    1.00       ea   
12   P-52620         GARNISH|Lime Mini Wedge    8.00    piece   
13   P-51510            SLICED|Avocado|1/4ea    4.00      PTN   
14   P-50398                 STICKS|Cucumber   12.00       CT   
15   P-61796         MARINADE|Bali Pork Chop   10.00       CT   
16   P-35713               BLACKENED|Chicken  185.00       ea   
17   P-51508              COOKED|Bacon|Slice    2.00    slice   
18   P-56795               COOKED|Burger 4oz    1.00       ea   
19   P-50809        YIELD|Country Loaf|Slice   18.00    slice   
20   P-50439                   FRIED|Tostada    3.00    piece   
21   P-57631           SKEWER|Greek Chicken     1.00     each   
22   P-26318                BAKEDPuff Pastry   10.00       ea   
23   P-61769          STEW|Chicken Pot Pie      8.00      PIE   
24   P-55238      MARINADE|Peri Peri Chicken  120.00       ea   
25   P-43635     ROASTED|Thai Chicken Thighs   25.00       ea   
26   P-37297              COOKED|Poached Egg    1.00     each   
27   P-53056          GRILLED|Roma Tomato|V2   13.00      PTN   
28   P-52222    YIELD|Pickle Spear ea 20-30g    1.00       ea   
29   P-26965        BAKED|Jalapeno Cornbread   12.00    piece   
30   P-28369                      COST|Bread    1.00       ea   
31   P-28372                    COST|Cheeses    1.00    slice   
32   P-28373                 COST|Vegetables    1.00       un   
33   P-52942          FILLING|Taco|Prawn|FLX    1.00     each   
34   P-51230           WINGS|Sauce Mix|ratio    1.00     srvg   
35   P-45255            YIELD|Chicken Strips   70.00    piece   
36   P-52994                YIELD|Prawn|TACO   35.00     each   
37   P-44392               PREP|Eggs|poached    8.00     each   
38   P-44506          SLICED|Avocado|Quarter    4.00     each   
39   P-43737             VEG|Soft Boiled Egg   20.00     each   
40   P-51826       GARNISH|Fried Rice Friday    1.00      PTN   
41   P-61508            GRILLED|Mexican Corn    8.00       ea   
42   P-46509               YIELD|Lettuce bun    3.00      PTN   
43    P-5548                    PREP|Lasagna    3.00  full in   
44    P-5960                   PREP|Tiramisu    1.00  full in   
45   P-61646              PREP|Chicken Wings  100.00       ea   
46   P-60970           SAND|IItalian Grander    1.00     each   
47   P-54644                  BAKED|Moussaka   16.00      PTN   
48   P-54667     BAKED|Pasta|Bolognese Penne   16.00      PTN   
49   P-53088      BATCH|Enchiladas Vegan|POP    6.00     each   
50   P-41727      BATCH|Lentil & Squash Stew   15.00      PTN   
51   P-62403           BATCH|RELLENO|Poblano    1.00     each   
52   P-53361           Batter|Pancake|Banana   24.00       ea   
53   P-51518        COOKED|4 oz Burger Patty    1.00      PTN   
54   P-55099        COOKED|6 oz Burger Patty    1.00      PTN   
55   P-47324         COOKED|Meatball Blended  180.00     each   
56   P-48863          DES|Brown Rice Pudding   12.00       CT   
57   P-51018          DOUGH|BreakfastBiscuit    5.00     each   
58   P-55422      FILLING|ChocCheeseCake|G&G    2.50       1L   
59   P-44353              FLEX|Savoury Chaat    7.00      PTN   
60   P-47610        FLEXlCyprus Mannoush 

### Get Preps with Nonstandard Unit

In [56]:
col_names = list(Preps.columns.values)
Preps_Nonstd = []

for index, row in Preps.iterrows():
    StdUom = Preps.loc[index,'StdUom']
    if StdUom not in ['g', 'ml']:
        Dict = {}
        Dict.update(dict(row))
        Preps_Nonstd.append(Dict)

Preps_Nonstd = pd.DataFrame(Preps_Nonstd, columns = col_names)

In [57]:
Preps_Nonstd

PrepId                     Description  PakQty PakUOM  \
0    P-61009           ALF|Flatbread|Brisket    1.00     un   
1    P-26965        BAKED|Jalapeno Cornbread   12.00  piece   
2    P-50502                  BAKED|Meatball  310.00   each   
3    P-54644                  BAKED|Moussaka   16.00    PTN   
4    P-54667     BAKED|Pasta|Bolognese Penne   16.00    PTN   
5    P-54785          BAKED|Puff Pastry Tart    6.00   each   
6    P-49184        BAKED|Tofu|Almond Butter    4.00    PTN   
7    P-32729             BAKED|Warm Baguette    4.00   each   
8    P-26318                BAKEDPuff Pastry   10.00     ea   
9    P-43206     BATCH| SMOOTHIE| Mango|16oz    4.00    PTN   
10   P-53088      BATCH|Enchiladas Vegan|POP    6.00   each   
11   P-26234      BATCH|Roasted Garlic Bread   16.00     ea   
12   P-29020  BATCH|SMOOTHIE|Wild Berry|16oz    4.00    PTN   
13   P-53754          BATCH|Whole Wheat Pita   15.00   each   
14   P-53361           BATTER|Pancake|Banana   24.00     ea   
15   P-35713               BLACKENED|Chicken  185.00     ea   
16   P-26047      BOILED|Hard Boiled Eggs FT   50.00     ea   
17   P-43663    BOWL|Cereal Breakfast Large     3.00    PTN   
18   P-43661    BOWL|Cereal Breakfast Small     3.00    PTN   
19   P-50725         BREAD|Focaccia|Portion    16.00     ea   
20   P-50379        BREADED|Cornmeal Catfish    1.00     CT   
21   P-32310  BS Xmas Cookies Shortbread 6ea    1.00  PAK 6   
22   P-46861     BUNS|Toasted slider hot dog   12.00   each   
23   P-49181   CHILI|B-Nut Squash & Chipotle    4.00    PTN   
24   P-13326             CK- XMAS SHORTBREAD   25.00     ea   
25   P-33556              COOKED| Fried Fish    1.00   each   
26   P-55099        COOKED|6 oz Burger Patty    1.00    PTN   
27   P-51508          COOKED|Bacon|(2) Slice    2.00  slice   
28   P-56795             COOKED|Burger 5.3oz    1.00     ea   
29   P-51134          COOKED|Hard Boiled Egg    2.00     un   
30   P-49178           COOKED|Mushroom|DSSTO    9.00    PTN   
31   P-37297              COOKED|Poached Egg    1.00   each   
32   P-56329              COOKED|Potato|Pave   36.00   each   
33   P-47814            COOKED|Salmon|Phyllo    1.00     ea   
34   P-55583             COOKED|Tamales|Meat   25.00   each   
35   P-55638         COOKED|Tamales|Mushroom   25.00   each   
36   P-60812               COOKED|Tart Shell    1.00   each   
37   P-28369                      COST|Bread    1.00     ea   
38   P-28372                    COST|Cheeses    1.00  slice   
39   P-28373                 COST|Vegetables    1.00     un   
40   P-22037     DES|Bar|Brownie Double Choc    1.00  slice   
41   P-22029                 DES|Bar|Nanaimo    1.00  slice   
42   P-22032      DES|Bar|Rocky Road Brownie    1.00  slice   
43   P-48485           DES|Bar|Salty Caramel    1.00  slice   
44   P-61132           DES|Bar|Tiger Brownie    1.00  slice   
45   P-61133    DES|Bar|Triple Berry Crumble    1.00  slice   
46   P-50510        DES|Bar|Triple Chocolate    1.00  slice   
47   P-22030           DES|Cake|Black Forest    1.00  slice   
48   P-60927        DES|Cake|Chocolate Layer    1.00  slice   
49   P-58285         DES|Cake|Slice Assorted    1.00    PTN   
50   P-22042       DES|Cake|Strawberry Cream    1.00  slice   
51   P-22049               DES|Cake|Tiramisu    1.00  slice   
52   P-33038                 DES|Jello|Asst.  240.00    PTN   
53   P-58297              DES|Pie|Asst Slice    1.00    PTN   
54   P-58286           DES|Square|Asst Whole    1.00    PTN   
55   P-56302                  DESSERT|Posset   60.00   each   
56   P-47243    DIMSUM|Veg. Spring Roll|1 pc    1.00    PTN   
57   P-51018          DOUGH|BreakfastBiscuit    5.00   each   
58   P-49177    FILLING|Shepherd's Pie|DSSTO    9.00    PTN   
59   P-52942          FILLING|Taco|Prawn|FLX    1.00   each   
60   P-26057        FRIED|Sunny/Overeasy Egg    1.00     ea   
61   P-50439                   FRIED|Tostada    3.00  piece   
62   P-58289       FRUIT|Canteloupe|1

In [58]:
# Filter out preps with nonstandard uom but have information already
Manual_PrepU = pd.read_csv(os.path.join(os.getcwd(), "data", "cleaning", "update", "Preps_UpdateUom.csv"))

col_names = list(Preps_Nonstd.columns.values)
Preps_Nonstd_na = []

for index, row in Preps_Nonstd.iterrows():
    PrepId = Preps_Nonstd.loc[index,'PrepId']
    if PrepId not in Manual_PrepU['PrepId'].values:
        Dict = {}
        Dict.update(dict(row))
        Preps_Nonstd_na.append(Dict)

Preps_Nonstd = pd.DataFrame(Preps_Nonstd_na, columns = col_names)
Preps_Nonstd

Empty DataFrame
Columns: [PrepId, Description, PakQty, PakUOM, InventoryGroup, StdQty, StdUom]
Index: []

In [59]:
path = os.path.join(os.getcwd(), "data", "cleaning", "Preps_NonstdUom.csv")
Preps_Nonstd.to_csv(path, index = False, header = True)

In [60]:
update_prep = pd.read_csv("data/cleaning/update/Preps_UpdateUom.csv")
update_prep

PrepId                     Description  PakQty   PakUOM  \
0    P-54697                 LEMON|Wedge 1/8    8.00     each   
1    P-35132      MARINATED|Lemon & Herb Chx  185.00       ea   
2    P-51992       YIELD|Bread|Sourdough 5/8   36.00    slice   
3    P-26234      BATCH|Roasted Garlic Bread   16.00       ea   
4    P-26170               GRILLED|NaanBread    1.00       ea   
5    P-16305              YIELD|Smokie (1pc)    1.00       ea   
6    P-26047      BOILED|Hard Boiled Eggs FT   50.00       ea   
7    P-26631      BRK|Pancake|Chocolate Chip   24.00       ea   
8    P-26057        FRIED|Sunny/Overeasy Egg    1.00       ea   
9    P-26056                  GRILLED|Tomato    1.00       ea   
10   P-44587                   GRL|FRIED|Egg    1.00       ea   
11   P-26481                POACHED|Egg|Soft    1.00       ea   
12   P-52620         GARNISH|Lime Mini Wedge    8.00    piece   
13   P-51510            SLICED|Avocado|1/4ea    4.00      PTN   
14   P-50398                 STICKS|Cucumber   12.00       CT   
15   P-61796         MARINADE|Bali Pork Chop   10.00       CT   
16   P-35713               BLACKENED|Chicken  185.00       ea   
17   P-51508              COOKED|Bacon|Slice    2.00    slice   
18   P-56795               COOKED|Burger 4oz    1.00       ea   
19   P-50809        YIELD|Country Loaf|Slice   18.00    slice   
20   P-50439                   FRIED|Tostada    3.00    piece   
21   P-57631           SKEWER|Greek Chicken     1.00     each   
22   P-26318                BAKEDPuff Pastry   10.00       ea   
23   P-61769          STEW|Chicken Pot Pie      8.00      PIE   
24   P-55238      MARINADE|Peri Peri Chicken  120.00       ea   
25   P-43635     ROASTED|Thai Chicken Thighs   25.00       ea   
26   P-37297              COOKED|Poached Egg    1.00     each   
27   P-53056          GRILLED|Roma Tomato|V2   13.00      PTN   
28   P-52222    YIELD|Pickle Spear ea 20-30g    1.00       ea   
29   P-26965        BAKED|Jalapeno Cornbread   12.00    piece   
30   P-28369                      COST|Bread    1.00       ea   
31   P-28372                    COST|Cheeses    1.00    slice   
32   P-28373                 COST|Vegetables    1.00       un   
33   P-52942          FILLING|Taco|Prawn|FLX    1.00     each   
34   P-51230           WINGS|Sauce Mix|ratio    1.00     srvg   
35   P-45255            YIELD|Chicken Strips   70.00    piece   
36   P-52994                YIELD|Prawn|TACO   35.00     each   
37   P-44392               PREP|Eggs|poached    8.00     each   
38   P-44506          SLICED|Avocado|Quarter    4.00     each   
39   P-43737             VEG|Soft Boiled Egg   20.00     each   
40   P-51826       GARNISH|Fried Rice Friday    1.00      PTN   
41   P-61508            GRILLED|Mexican Corn    8.00       ea   
42   P-46509               YIELD|Lettuce bun    3.00      PTN   
43    P-5548                    PREP|Lasagna    3.00  full in   
44    P-5960                   PREP|Tiramisu    1.00  full in   
45   P-61646              PREP|Chicken Wings  100.00       ea   
46   P-60970           SAND|IItalian Grander    1.00     each   
47   P-54644                  BAKED|Moussaka   16.00      PTN   
48   P-54667     BAKED|Pasta|Bolognese Penne   16.00      PTN   
49   P-53088      BATCH|Enchiladas Vegan|POP    6.00     each   
50   P-41727      BATCH|Lentil & Squash Stew   15.00      PTN   
51   P-62403           BATCH|RELLENO|Poblano    1.00     each   
52   P-53361           Batter|Pancake|Banana   24.00       ea   
53   P-51518        COOKED|4 oz Burger Patty    1.00      PTN   
54   P-55099        COOKED|6 oz Burger Patty    1.00      PTN   
55   P-47324         COOKED|Meatball Blended  180.00     each   
56   P-48863          DES|Brown Rice Pudding   12.00       CT   
57   P-51018          DOUGH|BreakfastBiscuit    5.00     each   
58   P-55422      FILLING|ChocCheeseCake|G&G    2.50       1L   
59   P-44353              FLEX|Savoury Chaat    7.00      PTN   
60   P-47610        FLEXlCyprus Mannoush 

***

## New Items

In [61]:
# Load current Items List with assigned Emission Factors Category ID
Items_Assigned = pd.read_csv(os.path.join(os.getcwd(), "data", "mapping", "Items_List_Assigned.csv"))
Items_Assigned.head()

ItemId  CategoryID               Description  CaseQty CaseUOM  PakQty  \
0  I-57545         1.0   CHUCK FLAT BONELESS FZN     3.30      Kg     1.0   
1  I-10869         1.0       BEEF STIRFRY COV FR     5.00      Kg     1.0   
2   I-7064         1.0     BEEF OUTSIDE FLAT AAA     1.00      Kg     1.0   
3  I-37005         1.0            BEEF MEATBALLS     4.54      Kg  1000.0   
4  I-37002         1.0  BEEF INSIDE ROUND SHAVED     9.00      Kg  1000.0   

  PakUOM InventoryGroup  
0     Kg           MEAT  
1     Kg           MEAT  
2     Kg           MEAT  
3      g           MEAT  
4      g           MEAT

In [62]:
Items_Assigned.shape

(2821, 8)

In [63]:
Items_Assigned["InventoryGroup"].unique()

array(['MEAT', 'DELI & PREPARED MEAT', 'FOOD - GROCERY', 'POULTRY',
       'PRODUCTION FOOD', 'DAIRY', 'BAKING-RAW INGREDIENTS', 'PRODUCE',
       'ICECREAM/NOVELTY/GELATO', 'SEAFOOD', 'CANDIES SNACKS', 'MISC.',
       'MM Grocery Cereal', 'BAKED GOODS', 'MM Grocery Chill', 'PREP',
       'BREAD', 'MM BAKERY', 'ZDONT USE FOOD', 'SPICES', 'FAIR TRADE',
       'MM Snack Ethnic', 'HM FROZEN SINGLE SERVE',
       'CHIPS, PRETZELS, NUTS', 'ZDONT USE FROZEN', 'BEVERAGE',
       'PACKAGED BEER, CIDER', 'LIQUOR', 'ALCOHOL - FOOD',
       'MM CANDY Chocolate ', 'PREGEL - ALL ITEMS',
       'HM SWEET & SAVOURY SNACKS', 'UCARE',
       'HM CHILL SINGLE SERVE BEVERAGE', 'JERKY, PEPPERONI', 'SUSHI',
       'MM CANDY Bulk', 'MM CANDY Gum & Mints', 'MM Snack Single Bars',
       'MERCHANDISE', 'MM Frozen Grocery', 'MM Frozen HMR', 'MM Grocery',
       'MM Grocery Coffee & Tea', 'MM Grocery Ethnic', 'MM Grocery Soup',
       'MM MERCH OTC', 'MM Snack Jerky', 'ZDONT USE CANDY - GUM & MINTS',
       'DI

In [64]:
Items_Assigned["CategoryID"].unique()

array([ 1.,  2.,  3.,  4.,  5.,  6.,  7.,  8.,  9., 10., 11., 12., 13.,
       14., 16., 17., 18., 19., 20., 21., 22., 23., 24., 25., 26., 27.,
       28., 30., 31., 32., 33., 34., 35., 36., 37., 38., 39., 40., 41.,
       42., 43., 44., 48., 49., 50., 51., 52., 53., 54., 55., 56., 57.,
       58., 59., 60., 61.])

In [65]:
Items_Assigned[Items_Assigned["CategoryID"] == 55]

ItemId  CategoryID                     Description  CaseQty  CaseUOM  \
1287  I-11794        55.0    YERBA MATE REVEL BERRY 458ML     12.0     each   
1288   I-1683        55.0         WATER VITAMIN ZERO XOXO     12.0    591ML   
1289   I-2955        55.0      WATER SPARKLING SAN PELLEG     24.0      PTN   
1290  I-52773        55.0    WATER SMART SPARKLING RASPB      12.0     each   
1291   I-5983        55.0               WATER FOR RECIPES      1.0        L   
1292  I-11671        55.0    WATER DASANI SPARKLING LEMON     12.0    355ML   
1293   I-1644        55.0              WATER DASANI 591ML     24.0    591ML   
1294  I-13982        55.0  TEA CHAI BOULDER CONCENT 3RDST      1.0      JUG   
1295  I-37651        55.0             TEA BLACK EARL GREY      6.0      box   
1296   I-1598        55.0         SODA SAN PELL LIMONATA      24.0    355ML   
1297   I-1590        55.0       SODA SAN PELL ARANCIATTA      24.0    355ML   
1298  I-11159        55.0        ODWALLA STRAW BANA 450ml      8.0     each   
1299  I-11158        55.0       ODWALLA MANGO TANGO 450ml      8.0       ea   
1300   I-1750        55.0       ODWALLA LIFEFOOD ORIGINAL      8.0    450ML   
1301   I-1821        55.0           JUICE PINEAPPLE TETRA     12.0   bottle   
1302  I-41738        55.0        JUICE PEACH SIMPLY 340ml     12.0     each   
1303   I-1820        55.0  JUICE ORANGE UNSWEETENED TETRA     12.0        L   
1304  I-13968        55.0      JUICE ORANGE SIMPLY  340ML     12.0       ea   
1305  I-43253        55.0           JUICE ORANGE MM 355ML     12.0    355ML   
1306  I-13967        55.0  JUICE LEMONADE SIMPLY RASPBERY     12.0    340ML   
1307  I-56154        55.0     JUICE LEMONADE SIMPLY 340ML     12.0    340ML   
1308   I-1690        55.0         JUICE LEMONADE MM 355ML     12.0    355ML   
1309  I-43255        55.0        JUICE CRAN MM CKTL 355ML     12.0    355ML   
1310  I-13969        55.0       JUICE APPLE SIMPLY  340ML      1.0    340ML   
1311   I-1686        55.0             JUICE APPLE MM 450M     24.0    450ML   
1312  I-43252        55.0            JUICE APPLE MM 355ML     12.0    355ML   
1313   I-1687        55.0            JUICE APPLE MM 341ML     12.0    341ML   
1314  I-43254        55.0             JUICE 5 ALIVE 355ML     12.0      can   
1315  I-46622        55.0         ICE TEA UNSWT GOLD PEAK     12.0       ea   
1316  I-46621        55.0         ICE TEA LEMON GOLD PEAK     12.0       ea   
1317  I-46620        55.0           ICE TEA GRN GOLD PEAK     12.0       ea   
1318   I-1642        55.0            COKE CLASSIC BIB 20L      1.0  BIB 20L   
1319   I-1639        55.0              COKE CLASSIC 500ML     24.0    500ML   
1320  I-56025        55.0  AHA WATER SP WATERMLN LIME PET     24.0     each   
1321  I-57484        55.0  AHA WATER SP PEACH HONEY PET       24.0     each   
1322  I-57285        55.0  AHA WATER BLUBRY POM SPARKLING     12.0     each   
1323  I-46554        55.0           MILK COCONUT ORIGINAL     12.0     each   
1324   I-3738        55.0       WATER COCONUT BLUE MONKEY     24.0    330ML   
1325  I-11672        55.0     WATER DASANI SPARKLING LIME     12.0   bottle   
1326  I-11673        55.0     WATER DASANI SPARKLING BERY     12.0    355ML   
1327   I-1634        55.0                 COKE ZERO 500ML     24.0    500ML   
1328   I-1674        55.0             WATER VITAMIN ESNTL     12.0    591ML   
1329   I-1775        55.0            HOT CHOC INSTANT PTN    300.0      PTN   
1330   I-1779        55.0           HOT CHOC LT INST PORT    300.0      pak   
1331   I-1792        55.0        JUICE APPLE CONC 6+1 TFC      4.0      JUG   
1332   I-1814        55.0       JUICE REALEMON PLAS 945ML     12.0    945ML   
1333   I-1816        55.0       JUICE ORANGE CONC 5+1 TFC      4.0      JUG   
1334   I-1827        55.0                JUICE TOMATO CAN      6.0   LG CAN   
1335   I-1863        55.0                     STEAZ PEACH     12.0    473ML   
1336   I-1865        55.0   STEAZ ZERO CAL CITRUS ICD TEA

### Get the List of New Items

In [66]:
# Filter new items by itemID that are not in the database and output them in a dataframe
col_names = list(Items.columns.values)
New_Items_List = []

for index, row in Items.iterrows():
    ItemId = Items.loc[index,'ItemId']
    if ItemId not in Items_Assigned['ItemId'].values:
        Dict = {}
        Dict.update(dict(row))
        New_Items_List.append(Dict)

New_Items = pd.DataFrame(New_Items_List, columns = col_names)

In [67]:
New_Items.insert(1, "CategoryID", '')
New_Items

Empty DataFrame
Columns: [ItemId, CategoryID, Description, CaseQty, CaseUOM, PakQty, PakUOM, InventoryGroup]
Index: []

In [68]:
New_Items.shape

(0, 8)

In [69]:
# Store the list of new items into .csv file
# If New_Items is not empty then we convert it to a csv file. 
if not New_Items.empty:
    path = os.path.join(os.getcwd(), "data", "mapping", "new items", str(datetime.date(datetime.now()))+"_New_Items.csv")
    New_Items.to_csv(path, index = False, header = True)

In [70]:
# file = pd.read_csv("data/mapping/new items/2022-11-01_New_Items.csv")
# file.to_excel("2022-11-01_New_Items.xlsx",index = None, header=True)
if not New_Items.empty:
    file = pd.read_csv("C:/Users/smvan/CFFS-S23/CFFS-22-23/data/mapping/new items/"+ str(datetime.date(datetime.now()))+"_New_Items.csv")
    file.to_excel(str(datetime.date(datetime.now()))+"_New_Items.xlsx",index = None, header=True)

In [71]:
# file2 = pd.read_excel("data/mapping/new items added/New_Items_Added_11.xlsx")
# file2.to_csv("data/mapping/new items added/New_Items_Added_11.csv", index=False)

file2 = pd.read_excel("data/mapping/new items added/New_Items_2023/New_Items_Added_2023_08_01.xlsx")
file2.to_csv("data/mapping/new items added/New_Items_2023/New_Items_Added_2023_08_01.csv", index=False)

***
## Data Summary

In [72]:
datasum = pd.DataFrame([New_Items.shape, Preps_Nonstd.shape, Items_Nonstd.shape],
                       columns = ['count', 'columns'], 
                       index = ['New_Items', 'Preps_Nonstd', 'Items_Nonstd'])
datasum

count  columns
New_Items         0        8
Preps_Nonstd      0        7
Items_Nonstd    360        7

In [73]:
print(New_Items.columns)

Index(['ItemId', 'CategoryID', 'Description', 'CaseQty', 'CaseUOM', 'PakQty',
       'PakUOM', 'InventoryGroup'],
      dtype='object')
